In [1]:
import pandas as pd
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score,root_mean_squared_error
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import numpy as np
from prophet import Prophet
import warnings
from sklearn.preprocessing import LabelEncoder
import lightgbm as lgb
from hyperopt import fmin, tpe, hp, Trials, STATUS_OK
warnings.filterwarnings("ignore")
from lightgbm import LGBMRegressor
import pickle

/Users/nadiatamayo/Library/Mobile Documents/com~apple~CloudDocs/BrainFood/Challenge/brainfoodchalleng/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
df=pd.read_csv('demandahistorica_procesada.csv')
df['fecha']=pd.to_datetime(df['fecha'])
df = df.sort_values(by=['prod_id', 'fecha'])
df['lag_fecha_inv'] = df.groupby('prod_id')['fecha'].shift(-1)
df['lag_ventas_inv'] = df.groupby('prod_id')['ventas'].shift(-1)
df['lag_modelo_actual_inv'] = df.groupby('prod_id')['modelo_actual'].shift(-1)

## Evaluación del modelo actual

In [3]:

df['residuals'] = df['ventas'] - df['modelo_actual']
fig = go.Figure()
fig.add_trace(go.Scatter(x=df['fecha'], y=df['residuals'], mode='markers', 
                         marker=dict(color='red'), name='Residuals'))

fig.add_shape(type="line",
              x0=df['fecha'].min(), y0=0, x1=df['fecha'].max(), y1=0,
              line=dict(color="black", width=2, dash="dash"))

fig.update_layout(
    title="Residuos (Ventas - Modelo Actual) a través del tiempo",
    xaxis_title="Año-Mes",
    yaxis_title="Residuals",
    xaxis_tickangle=45,
    showlegend=True,
    legend=dict(x=0.01, y=0.99),
    width=1200,  
    height=400   
)

fig.update_xaxes(showgrid=True)
fig.update_yaxes(showgrid=True)

fig.show()

Se puede observar que los residuales más altos están de igual forma en los meses que se tienen picos más altos de ventas estacionales que son de diciembre a febrero, por lo cuál el modelo actual no está logrando captar estos patrones estacionales que se ven claros dentro de la dinámica de la empresa.

In [4]:
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import numpy as np

y_true = df['ventas']
y_pred = df['modelo_actual']

mae = mean_absolute_error(y_true, y_pred)
r2 = r2_score(y_true, y_pred)
mse = root_mean_squared_error(y_true, y_pred)

metricas_modeloactual = {
    'RMSE': mse,
    'MAE': mae,
    'R-squared': r2
}

print(metricas_modeloactual)


{'RMSE': 553.343353560499, 'MAE': 393.26522261168714, 'R-squared': 0.403582023675239}


Cómo se puede observar el modelo actual en promedio las predicciones del modelo difieren por aproximadamente 393 unidades en ventas de los valores reales y el modelo está explicando aproximadamenteo el 40% de la variabilidad de las ventas , lo cual sugiere que puede mejorarse, principalmente en los periodos de picos de ventas de diciembre a febrero en cada ciclo anual. 

Debido a que nos importa que el modelo esté realizando las predicciones de manera adecuada , vamos a tomar como test el año de 2023 y vamos a entrenar los datos desde 2018 que comenzaron a estabilizarse la cantidad de ventas realizadas. Por lo cuál la evaluación del modelo la realizaremos con el último año que son la predicciones que más nos interesan y con las cuáles podemos compara las evaluaciones en la misma temporalidad, así como los productos que se están vendiendo hasta 2023-12, no vamos a tomar en cuenta los productos que ya no se están vendiendo

In [5]:
max_date = df['fecha'].max()
products_with_sales_at_max_date = df[df['fecha'] == max_date]['prod_id'].unique()
df_training = df[df['prod_id'].isin(products_with_sales_at_max_date)]

In [6]:
df_agrupado=df_training.groupby('fecha').agg(
    {'ventas':sum,'modelo_actual':sum}).reset_index()
y_true = df_agrupado.loc[(df_agrupado['fecha']>='2022-12-01')  & (df_agrupado['fecha']<='2023-12-01')]['ventas']
y_pred = df_agrupado.loc[(df_agrupado['fecha']>='2022-12-01') & (df_agrupado['fecha']<='2023-12-01')]['modelo_actual']

mae = mean_absolute_error(y_true, y_pred)
r2 = r2_score(y_true, y_pred)
mse = root_mean_squared_error(y_true, y_pred)

metricas_modeloactual_2023 = {
    'RMSE': mse,
    'MAE': mae,
    'R-squared': r2
}

print(metricas_modeloactual_2023)

{'RMSE': 234505.76645384697, 'MAE': 161740.7689406999, 'R-squared': 0.15909660721521002}


## Implementación modelo nuevo

In [7]:
df_training

fecha  prod_id  precio_promedio  ventas  modelo_actual   año  \
0     2017-01-01        0      6651.737920  1786.0    1943.551087  2017   
1     2017-02-01        0      4919.698602  2194.0    1853.111850  2017   
2     2017-03-01        0      3277.484704  1178.0    1659.733052  2017   
3     2017-04-01        0      5906.864332  1010.0    1580.492875  2017   
4     2017-05-01        0      4662.644018  1327.0    1552.062093  2017   
...          ...      ...              ...     ...            ...   ...   
80719 2023-08-01      998     12905.955323   535.0     464.894091  2023   
80720 2023-09-01      998     10690.792563   645.0     611.003111  2023   
80721 2023-10-01      998     11975.369686   456.0     600.803486  2023   
80722 2023-11-01      998     10963.791973   827.0     572.086823  2023   
80723 2023-12-01      998      9080.789381  1906.0    1030.493505  2023   

       añoymes año_trimestre  ventaspreciopromedio lag_fecha_inv  \
0      2017-01        2017Q1          1.188000e+07    2017-02-01   
1      2017-02        2017Q1          1.079382e+07    2017-03-01   
2      2017-03        2017Q1          3.860877e+06    2017-04-01   
3      2017-04        2017Q2          5.965933e+06    2017-05-01   
4      2017-05        2017Q2          6.187329e+06    2017-06-01   
...        ...           ...                   ...           ...   
80719  2023-08        2023Q3          6.904686e+06    2023-09-01   
80720  2023-09        2023Q3          6.895561e+06    2023-10-01   
80721  2023-10        2023Q4          5.460769e+06    2023-11-01   
80722  2023-11        2023Q4          9.067056e+06    2023-12-01   
80723  2023-12        2023Q4          1.730798e+07           NaT   

       lag_ventas_inv  lag_modelo_actual_inv   residuals  
0              2194.0            1853.111850 -157.551087  
1              1178.0            1659.733052  340.888150  
2              1010.0            1580.492875 -481.733052  
3              1327.0            1552.062093 -570.492875  
4               982.0            1108.069873 -225.062093  
...               ...                    ...         ...  
80719           645.0             611.003111   70.105909  
80720           456.0             600.803486   33.996889  
80721           827.0             572.086823 -144.803486  
80722          1906.0            1030.493505  254.913177  
80723             NaN                    NaN  875.506495  

[61032 rows x 13 columns]

In [8]:
df_trainingProphet=df_training[['fecha','prod_id','ventas','precio_promedio','modelo_actual']]

### Prophet 
Se utilizará probar el primer modelo con Prophet ya que es útil para series de tiempo con efectos estacionales marcados como los que observamos en nuestros datos

In [9]:
import pandas as pd
from prophet import Prophet
from concurrent.futures import ProcessPoolExecutor
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
import numpy as np

def entrenar_y_predecir_producto(prod_id, train_data, test_data):
    group = train_data[train_data['prod_id'] == prod_id]

    if group.empty:
        print(f"No training data available for product {prod_id}")
        return prod_id, {'MAE': None, 'RMSE': None, 'R-squared': None}
    
    df_prophet_train = group[['fecha', 'ventas']].copy()
    df_prophet_train.columns = ['ds', 'y']

   
    model = Prophet(yearly_seasonality=True)
    model.fit(df_prophet_train)

    
    
    test_group = test_data[test_data['prod_id'] == prod_id]
    if test_group.empty:
        print(f"No test data available for product {prod_id}")
        return prod_id, {'MAE': None, 'RMSE': None, 'R-squared': None}
    
    future = model.make_future_dataframe(periods=len(test_group), freq='ME')
    forecast = model.predict(future)
    forecast['ds'] = forecast['ds'] + pd.offsets.MonthBegin(1)
    forecast = forecast.drop_duplicates(subset=['ds'])
    forecast_2023 = forecast[forecast['ds'].isin(test_group['fecha'])]
    
    y_true = test_group['ventas'].values
    y_pred = forecast_2023['yhat'].values
    test_group['y_pred']=y_pred

    mae = mean_absolute_error(y_true, y_pred)
    rmse = np.sqrt(mean_squared_error(y_true, y_pred))
    r2 = r2_score(y_true, y_pred)
    
    return prod_id, {'MAE': mae, 'RMSE': rmse, 'R-squared': r2}, test_group[['fecha', 'y_pred','prod_id','modelo_actual','ventas']]

train_data = df_trainingProphet[(df_trainingProphet['fecha'] >= '2018-01-01') & (df_trainingProphet['fecha'] < '2023-01-01')]
test_data = df_trainingProphet[(df_trainingProphet['fecha'] >= '2023-01-01')]

def process_product(prod_id):
    return entrenar_y_predecir_producto(prod_id, train_data, test_data)

from concurrent.futures import ThreadPoolExecutor

with ThreadPoolExecutor() as executor:
    resultados = list(executor.map(process_product,df_trainingProphet['prod_id'].unique() ))

metricas_por_producto = {}
predicciones_global = pd.DataFrame()

for prod_id, metricas, predicciones in resultados:
    metricas_por_producto[prod_id] = metricas
    
    
    predicciones_global = pd.concat([predicciones_global, predicciones], ignore_index=True)


16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] start processing
16:33:44 - cmdstanpy - INFO - Chain [1] done processing
16:33:44 - cmdstanpy - INFO - Chain [1] done processing
16:33:44 - cmdstanpy - INFO - Chain [1] done processing
16:33:44 - cmdstanpy - INFO - Chain [1] done processing
16:33:44 - cmdstanpy - INFO - Chain [1] done processing
16:33:44 - cmdstanpy - INFO - Chain 

In [10]:
mae = mean_absolute_error(predicciones_global['ventas'], predicciones_global['modelo_actual'])
r2 = r2_score(predicciones_global['ventas'], predicciones_global['modelo_actual'])
mse = root_mean_squared_error(predicciones_global['ventas'], predicciones_global['modelo_actual'])

metricas_modeloactual_2023 = {
    'RMSE': mse,
    'MAE': mae,
    'R-squared': r2
}

print(metricas_modeloactual_2023)

{'RMSE': 619.3245420029234, 'MAE': 441.9707476762292, 'R-squared': 0.38278979157145165}


In [11]:
mae = mean_absolute_error(predicciones_global['ventas'], predicciones_global['y_pred'])
r2 = r2_score(predicciones_global['ventas'], predicciones_global['y_pred'])
mse = root_mean_squared_error(predicciones_global['ventas'], predicciones_global['y_pred'])

metricas_modelo_prophet = {
    'RMSE': mse,
    'MAE': mae,
    'R-squared': r2
}

print(metricas_modelo_prophet)

{'RMSE': 1105.375459460135, 'MAE': 817.5822225919028, 'R-squared': -0.9661477801549527}


### Implementación modelo LightGBM

In [12]:
#Función para realizar lags de las variables disponibles
def Lag_functions(dt, lags=[1], wins=[3, 6, 12], column=None):
    lag_cols = [f"lag_{lag}_{column}" for lag in lags]
    for lag, lag_col in zip(lags, lag_cols):
        dt[lag_col] = dt.groupby("prod_id")[column].shift(lag).fillna(-1)

    for win in wins:
        for lag, lag_col in zip(lags, lag_cols):
            dt[f"rmean_{column}_{lag}_{win}"] = dt.groupby("prod_id")[lag_col].transform(lambda x: x.rolling(win).mean()).fillna(-1)

    return dt


In [13]:
df_traininglgm=Lag_functions(df_training, column='ventas')
df_traininglgm=Lag_functions(df_training, column='precio_promedio')
df_traininglgm['mes_numero'] = df_traininglgm['fecha'].dt.month

In [14]:
df_traininglgm

fecha  prod_id  precio_promedio  ventas  modelo_actual   año  \
0     2017-01-01        0      6651.737920  1786.0    1943.551087  2017   
1     2017-02-01        0      4919.698602  2194.0    1853.111850  2017   
2     2017-03-01        0      3277.484704  1178.0    1659.733052  2017   
3     2017-04-01        0      5906.864332  1010.0    1580.492875  2017   
4     2017-05-01        0      4662.644018  1327.0    1552.062093  2017   
...          ...      ...              ...     ...            ...   ...   
80719 2023-08-01      998     12905.955323   535.0     464.894091  2023   
80720 2023-09-01      998     10690.792563   645.0     611.003111  2023   
80721 2023-10-01      998     11975.369686   456.0     600.803486  2023   
80722 2023-11-01      998     10963.791973   827.0     572.086823  2023   
80723 2023-12-01      998      9080.789381  1906.0    1030.493505  2023   

       añoymes año_trimestre  ventaspreciopromedio lag_fecha_inv  ...  \
0      2017-01        2017Q1          1.188000e+07    2017-02-01  ...   
1      2017-02        2017Q1          1.079382e+07    2017-03-01  ...   
2      2017-03        2017Q1          3.860877e+06    2017-04-01  ...   
3      2017-04        2017Q2          5.965933e+06    2017-05-01  ...   
4      2017-05        2017Q2          6.187329e+06    2017-06-01  ...   
...        ...           ...                   ...           ...  ...   
80719  2023-08        2023Q3          6.904686e+06    2023-09-01  ...   
80720  2023-09        2023Q3          6.895561e+06    2023-10-01  ...   
80721  2023-10        2023Q4          5.460769e+06    2023-11-01  ...   
80722  2023-11        2023Q4          9.067056e+06    2023-12-01  ...   
80723  2023-12        2023Q4          1.730798e+07           NaT  ...   

        residuals  lag_1_ventas  rmean_ventas_1_3  rmean_ventas_1_6  \
0     -157.551087          -1.0         -1.000000         -1.000000   
1      340.888150        1786.0         -1.000000         -1.000000   
2     -481.733052        2194.0       1326.333333         -1.000000   
3     -570.492875        1178.0       1719.333333         -1.000000   
4     -225.062093        1010.0       1460.666667         -1.000000   
...           ...           ...               ...               ...   
80719   70.105909         590.0        502.666667        555.500000   
80720   33.996889         535.0        538.666667        474.833333   
80721 -144.803486         645.0        590.000000        518.333333   
80722  254.913177         456.0        545.333333        524.000000   
80723  875.506495         827.0        642.666667        590.666667   

       rmean_ventas_1_12  lag_1_precio_promedio  rmean_precio_promedio_1_3  \
0              -1.000000              -1.000000                  -1.000000   
1              -1.000000            6651.737920                  -1.000000   
2              -1.000000            4919.698602                3856.812174   
3              -1.000000            3277.484704                4949.640409   
4              -1.000000            5906.864332                4701.349213   
...                  ...                    ...                        ...   
80719         950.250000           13067.095891               11366.730534   
80720         968.750000           12905.955323               11678.199348   
80721         965.583333           10690.792563               12221.281259   
80722         928.833333           11975.369686               11857.372524   
80723         914.000000           10963.791973               11209.984740   

       rmean_precio_promedio_1_6  rmean_precio_promedio_1_12  mes_numero  
0                      -1.000000                   -1.000000           1  
1                      -1.000000                   -1.000000           2  
2                      -1.000000                   -1.000000           3  
3                      -1.000000                   -1.000000           4  
4                      -1.000000                   -1.000000        

In [15]:
cat_feats = ['prod_id']
for encoded in cat_feats:
    le = LabelEncoder()
    df_traininglgm[encoded] = le.fit_transform(df_traininglgm[encoded])

In [16]:
df_traininglgm.columns

Index(['fecha', 'prod_id', 'precio_promedio', 'ventas', 'modelo_actual', 'año',
       'añoymes', 'año_trimestre', 'ventaspreciopromedio', 'lag_fecha_inv',
       'lag_ventas_inv', 'lag_modelo_actual_inv', 'residuals', 'lag_1_ventas',
       'rmean_ventas_1_3', 'rmean_ventas_1_6', 'rmean_ventas_1_12',
       'lag_1_precio_promedio', 'rmean_precio_promedio_1_3',
       'rmean_precio_promedio_1_6', 'rmean_precio_promedio_1_12',
       'mes_numero'],
      dtype='object')

In [17]:
df_traininglgm_final=df_traininglgm[['lag_fecha_inv', 'prod_id','ventas','rmean_ventas_1_3', 'rmean_ventas_1_12',
       'rmean_precio_promedio_1_3', 'rmean_precio_promedio_1_12', 
       'lag_1_ventas', 'lag_1_precio_promedio', 'rmean_ventas_1_6',
       'rmean_precio_promedio_1_6', 'mes_numero','modelo_actual','lag_ventas_inv','fecha','lag_modelo_actual_inv']]
df_traininglgm_final.head()
df_traininglgm_final.dropna(subset='lag_fecha_inv', inplace=True)
df_traininglgm_final=df_traininglgm_final.loc[df_traininglgm_final['fecha']>="2015-01-01"]

In [18]:
train_data_lgb = df_traininglgm_final.loc[(df_traininglgm_final['fecha'] <= '2022-11-01')]


xtrain_data_lgb_final = train_data_lgb[['prod_id', 'rmean_ventas_1_3', 'rmean_ventas_1_12',
                                        'rmean_precio_promedio_1_3', 'mes_numero',
                                        'lag_1_ventas', 'lag_1_precio_promedio', 'ventas']]
ytrain_label = train_data_lgb['lag_ventas_inv']

test_data_lgb = df_traininglgm_final[(df_traininglgm_final['fecha'] >= '2022-12-01') & 
                                     (df_traininglgm_final['fecha'] < '2023-12-01')]
xtest_data_lgb_final = test_data_lgb[['prod_id', 'rmean_ventas_1_3', 'rmean_ventas_1_12',
                                      'rmean_precio_promedio_1_3', 'mes_numero',
                                      'lag_1_ventas', 'lag_1_precio_promedio', 'ventas']]
ytest_data_label = test_data_lgb['lag_ventas_inv']

In [19]:
dtrainlgbm = lgb.Dataset(xtrain_data_lgb_final , label = ytrain_label,  free_raw_data=False)
dtestlgbm = lgb.Dataset(xtest_data_lgb_final, label = ytest_data_label,   reference=dtrainlgbm)

In [20]:
params = {
        "objective" : "regression",
        "metric" : "rmse",
        "learning_rate" : 0.075,
        "sub_feature" : 0.8,
        "sub_row" : 0.75,
        "bagging_freq" : 1,
        "lambda_l2" : 0.1,
        'verbosity': 1,
       'num_iterations' : 1000,        
        'num_leaves': 128,
        "min_data_in_leaf": 50,
}
m_lgb_baseline= lgb.train(
    params,
    train_set=dtrainlgbm,
    valid_sets=[dtrainlgbm, dtestlgbm],  
    num_boost_round=150
)

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000635 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1796
[LightGBM] [Info] Number of data points in the train set: 48661, number of used features: 8
[LightGBM] [Info] Start training from score 1100.418590


In [21]:
y_pred = m_lgb_baseline.predict(xtest_data_lgb_final, num_iteration=m_lgb_baseline.best_iteration)
test_data_lgb['predictions']=y_pred

In [22]:
mae_baseline = mean_absolute_error(test_data_lgb['lag_ventas_inv'], test_data_lgb['predictions'])
r2_baseline = r2_score(test_data_lgb['lag_ventas_inv'], test_data_lgb['predictions'])
rmse_baseline = root_mean_squared_error(test_data_lgb['lag_ventas_inv'], test_data_lgb['predictions'])

metricas_modeloactual_baseline = {
    'RMSE': rmse_baseline,
    'MAE': mae_baseline,
    'R-squared': r2_baseline
}

print(metricas_modeloactual_baseline)

{'RMSE': 607.5182538552127, 'MAE': 437.02921182413075, 'R-squared': 0.40609745916905726}


In [23]:
mae = mean_absolute_error(test_data_lgb['lag_ventas_inv'], test_data_lgb['lag_modelo_actual_inv'])
r2 = r2_score(test_data_lgb['lag_ventas_inv'], test_data_lgb['lag_modelo_actual_inv'])
mse = root_mean_squared_error(test_data_lgb['lag_ventas_inv'], test_data_lgb['lag_modelo_actual_inv'])

metricas_modeloactual = {
    'RMSE': mse,
    'MAE': mae,
    'R-squared': r2
}

print(metricas_modeloactual)

{'RMSE': 619.3245420029234, 'MAE': 441.9707476762292, 'R-squared': 0.38278979157145165}


### Hyperparameter tunning

In [24]:
def objective(params):
  
    lgbm = lgb.LGBMRegressor(
        n_estimators=1000,
        **params
    )
    lgbm.fit(xtrain_data_lgb_final, ytrain_label, eval_set=[(xtest_data_lgb_final, ytest_data_label)])

    preds = lgbm.predict(xtest_data_lgb_final)
    
    rmse = np.sqrt(np.mean((preds - ytest_data_label) ** 2))

    return {'loss': rmse, 'status': STATUS_OK}


In [25]:
search_space = {
    'num_leaves': hp.choice('num_leaves', [31, 50, 100, 150, 200]),
    'max_depth': hp.choice('max_depth', [-1, 10, 20, 30]),
    'learning_rate': hp.uniform('learning_rate', 0.01, 0.3),
    'min_data_in_leaf': hp.choice('min_data_in_leaf', [20, 30, 50, 100]),  
    'bagging_fraction': hp.uniform('bagging_fraction', 0.7, 1.0),  
    'feature_fraction': hp.uniform('feature_fraction', 0.7, 1.0),  
    'lambda_l2': hp.uniform('lambda_l2', 0.0, 1.0),  
}



In [26]:
trials = Trials()

best_params = fmin(
    fn=objective,  
    space=search_space,  
    algo=tpe.suggest,  
    max_evals=100,
    trials=trials,  
    rstate=np.random.default_rng(42)  
)

[LightGBM] [Warning] feature_fraction is set=0.9303569193296128, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9303569193296128
[LightGBM] [Warning] bagging_fraction is set=0.7341388801550821, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7341388801550821
[LightGBM] [Warning] lambda_l2 is set=0.6517423997488939, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.6517423997488939
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] feature_fraction is set=0.9303569193296128, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.9303569193296128
[LightGBM] [Warning] bagging_fraction is set=0.7341388801550821, subsample=1.0 will be ignored. Current value: bagging_fraction=0.7341388801550821
[LightGBM] [Warning] lambda_l2 is set=0.6517423997488939, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.6517423997488939
[Light

In [27]:
best_params['num_leaves'] = max(2, best_params.get('num_leaves', 31))

In [28]:
best_params

{'bagging_fraction': 0.8018252091633248,
 'feature_fraction': 0.784806087218487,
 'lambda_l2': 0.3585619546874841,
 'learning_rate': 0.011095793073911106,
 'max_depth': 1,
 'min_data_in_leaf': 2,
 'num_leaves': 2}

In [36]:
lgbm_tunned = lgb.LGBMRegressor(
        n_estimators=1000,
      **best_params
    )
lgbm_tunned.fit(xtrain_data_lgb_final, ytrain_label, eval_set=[(xtest_data_lgb_final, ytest_data_label)])

preds_tunned = lgbm_tunned.predict(xtest_data_lgb_final)
    
rmse = np.sqrt(np.mean((preds_tunned - ytest_data_label) ** 2))

[LightGBM] [Warning] feature_fraction is set=0.784806087218487, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.784806087218487
[LightGBM] [Warning] bagging_fraction is set=0.8018252091633248, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8018252091633248
[LightGBM] [Warning] lambda_l2 is set=0.3585619546874841, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.3585619546874841
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2
[LightGBM] [Warning] feature_fraction is set=0.784806087218487, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.784806087218487
[LightGBM] [Warning] bagging_fraction is set=0.8018252091633248, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8018252091633248
[LightGBM] [Warning] lambda_l2 is set=0.3585619546874841, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.3585619546874841
[LightGBM] [Wa

In [43]:
test_data_lgb['predictions_tunned']=preds_tunned

#### Evaluación Modelo Actual vs Modelo Nuevo

In [44]:
mae_tunned = mean_absolute_error(test_data_lgb['lag_ventas_inv'], test_data_lgb['predictions_tunned'])
r2_tunned = r2_score(test_data_lgb['lag_ventas_inv'], test_data_lgb['predictions_tunned'])
mse_tunned = root_mean_squared_error(test_data_lgb['lag_ventas_inv'], test_data_lgb['predictions_tunned'])

metricas_modeloactual_tunned = {
    'RMSE': mse_tunned,
    'MAE': mae_tunned,
    'R-squared': r2_tunned
}

print(metricas_modeloactual_tunned)

{'RMSE': 607.6552732078472, 'MAE': 441.88390096461075, 'R-squared': 0.4058295320148603}


In [46]:
mae_baseline_not_tunned = mean_absolute_error(test_data_lgb['lag_ventas_inv'], test_data_lgb['predictions'])
r2_baseline_not_tunned = r2_score(test_data_lgb['lag_ventas_inv'], test_data_lgb['predictions'])
mse_baseline_not_tunned  = root_mean_squared_error(test_data_lgb['lag_ventas_inv'], test_data_lgb['predictions'])

metricas_baseline_not_tunned  = {
    'RMSE': mse_baseline_not_tunned,
    'MAE': mae_baseline_not_tunned,
    'R-squared': r2_baseline_not_tunned
}

print(metricas_baseline_not_tunned)

{'RMSE': 607.5182538552127, 'MAE': 437.02921182413075, 'R-squared': 0.40609745916905726}


In [47]:
with open('lgbm_tuned_model.pkl', 'wb') as file:
    pickle.dump(lgbm_tunned, file)

In [57]:
test_data_lgb_grouped=test_data_lgb.groupby('lag_fecha_inv').agg(
    {'lag_ventas_inv':'sum',
     'lag_modelo_actual_inv':'sum',
     'predictions_tunned':'sum'}
).reset_index()

In [58]:

fig = go.Figure()

fig.add_trace(go.Scatter(x=test_data_lgb_grouped['lag_fecha_inv'], y=test_data_lgb_grouped['lag_ventas_inv'], 
                         mode='lines+markers', name='Ventas'))
fig.add_trace(go.Scatter(x=test_data_lgb_grouped['lag_fecha_inv'], y=test_data_lgb_grouped['lag_modelo_actual_inv'], 
                         mode='lines+markers', name='Modelo Actual'))
fig.add_trace(go.Scatter(x=test_data_lgb_grouped['lag_fecha_inv'], y=test_data_lgb_grouped['predictions_tunned'], 
                         mode='lines+markers', name='Predicciones Ajustadas-LightGBM'))

fig.update_layout(
    title='Comparación de Modelos vs Ventas',
    xaxis_title='Fecha',
    yaxis_title='Valor',
    legend_title='Modelos',
    template='plotly_white'
)

fig.show()


In [59]:
test_data_lgb_grouped['diferencia_ventas_modeloactual']= test_data_lgb_grouped['lag_ventas_inv']-test_data_lgb_grouped['lag_modelo_actual_inv']
test_data_lgb_grouped['diferencia_ventas_modelonuevo']= test_data_lgb_grouped['lag_ventas_inv']-test_data_lgb_grouped['predictions_tunned']

In [60]:
mae_current = round(mean_absolute_error(test_data_lgb_grouped['lag_ventas_inv'], test_data_lgb_grouped['lag_modelo_actual_inv']),2)
rmse_current = round(np.sqrt(mean_squared_error(test_data_lgb_grouped['lag_ventas_inv'], test_data_lgb_grouped['lag_modelo_actual_inv'])),2)

mae_tuned = round(mean_absolute_error(test_data_lgb_grouped['lag_ventas_inv'], test_data_lgb_grouped['predictions_tunned']),2)
rmse_tuned = round(np.sqrt(mean_squared_error(test_data_lgb_grouped['lag_ventas_inv'], test_data_lgb_grouped['predictions_tunned'])),2)

metrics_df = pd.DataFrame({
    'Model': ['Modelo actual', 'Modelo Nuevo'],
    'MAE': [mae_current, mae_tuned],
    'RMSE': [rmse_current, rmse_tuned]
})

metrics_df['MAE_Indicator'] = ['↑' if mae_current > mae_tuned else '↓', '↑' if mae_tuned > mae_current else '↓']
metrics_df['RMSE_Indicator'] = ['↑' if rmse_current > rmse_tuned else '↓', '↑' if rmse_tuned > rmse_current else '↓']

metrics_df['MAE'] = metrics_df.apply(lambda x: f"{x['MAE']} {x['MAE_Indicator']}", axis=1)
metrics_df['RMSE'] = metrics_df.apply(lambda x: f"{x['RMSE']} {x['RMSE_Indicator']}", axis=1)


metrics_df = metrics_df[['Model', 'MAE', 'RMSE']]
metrics_df

Model          MAE         RMSE
0  Modelo actual  143199.17 ↑  217422.03 ↑
1   Modelo Nuevo   34947.89 ↓   52083.77 ↓

In [61]:
test_data_lgb_grouped['abs_error_current'] = np.abs(test_data_lgb_grouped['lag_ventas_inv'] - test_data_lgb_grouped['lag_modelo_actual_inv'])
test_data_lgb_grouped['abs_error_tuned'] = np.abs(test_data_lgb_grouped['lag_ventas_inv'] - test_data_lgb_grouped['predictions_tunned'])


test_data_lgb_grouped['cumulative_error_actual'] = test_data_lgb_grouped['abs_error_current'].cumsum()
test_data_lgb_grouped['cumulative_error_nuevo'] = test_data_lgb_grouped['abs_error_tuned'].cumsum()


In [63]:

fig = go.Figure()

fig.add_trace(go.Scatter(x=test_data_lgb_grouped['lag_fecha_inv'], y=test_data_lgb_grouped['cumulative_error_actual'], 
                         mode='lines+markers', 
                         name='Modelo Actual', 
                         line=dict(color='blue')))
fig.add_trace(go.Scatter(x=test_data_lgb_grouped['lag_fecha_inv'], y=test_data_lgb_grouped['cumulative_error_nuevo'], 
                         mode='lines+markers', 
                         name='Modelo Nuevo', 
                         line=dict(color='green')))

fig.update_layout(
    title='Error acumulativo para predicciones de 2023',
    xaxis_title='Año-Mes',
    yaxis_title='Error acumulativo',
    legend_title='Modelo',
    xaxis=dict(tickformat='%Y-%m')
)

fig.show()


In [64]:
revenue_gain_permodels=pd.merge(test_data_lgb[['lag_fecha_inv','prod_id','lag_ventas_inv','lag_modelo_actual_inv','predictions_tunned']],df[['lag_fecha_inv','prod_id','precio_promedio']], on=['lag_fecha_inv','prod_id'])
revenue_gain_permodels['residuales_modeloactual']=revenue_gain_permodels['lag_ventas_inv']-revenue_gain_permodels['lag_modelo_actual_inv']
revenue_gain_permodels['residuales_modelonuevo']=revenue_gain_permodels['lag_ventas_inv']-revenue_gain_permodels['predictions_tunned']
revenue_gain_permodels['ganancia/perdida_modeloactual']=revenue_gain_permodels['precio_promedio']*revenue_gain_permodels['residuales_modeloactual']
revenue_gain_permodels['ganancia/perdida_modelonuevo']=revenue_gain_permodels['precio_promedio']*revenue_gain_permodels['residuales_modelonuevo']

In [67]:
test_data_lgb['residuales_modeloactual']=test_data_lgb['lag_ventas_inv']-test_data_lgb['lag_modelo_actual_inv']
test_data_lgb['residuales_modelonuevo']=test_data_lgb['lag_ventas_inv']-test_data_lgb['predictions_tunned']

In [69]:
fig = go.Figure()



fig.add_trace(go.Scatter(
    x=test_data_lgb['lag_fecha_inv'], 
    y=test_data_lgb['residuales_modeloactual'], 
    mode='markers', 
    marker=dict(color='red'), 
    name='Residuales modelo actual'
))

fig.add_trace(go.Scatter(
    x=test_data_lgb['lag_fecha_inv'], 
    y=test_data_lgb['residuales_modelonuevo'], 
    mode='markers', 
    marker=dict(color='blue'),  
    name='Residuales modelo nuevo'
))

fig.add_shape(type="line",
              x0=revenue_gain_permodels['lag_fecha_inv'].min(), 
              y0=0, 
              x1=revenue_gain_permodels['lag_fecha_inv'].max(), 
              y1=0,
              line=dict(color="black", width=2, dash="dash"))


fig.update_layout(
    title="Errores de predicción Modelo Nuevo vs Modelo Actual para 2023",
    xaxis_title="Año-Mes",
    yaxis_title="Residuals",
    xaxis_tickangle=45,
    showlegend=True,
    legend=dict(x=0.01, y=0.99),
    width=1200,
    height=400
)


fig.update_xaxes(showgrid=True)
fig.update_yaxes(showgrid=True)


fig.show()


In [70]:

avg_gain_loss_actual = revenue_gain_permodels['ganancia/perdida_modeloactual'].mean()
avg_gain_loss_tunned = revenue_gain_permodels['ganancia/perdida_modelonuevo'].mean()

gain_loss_improvement = avg_gain_loss_tunned - avg_gain_loss_actual

results = {
    'Promedio de estimación de ganacias modelo actual': avg_gain_loss_actual,
    'Promedio de estimación de ganacias modelo nuevo': avg_gain_loss_tunned,
}

results


{'Promedio de estimación de ganacias modelo actual': -15101.479520508694,
 'Promedio de estimación de ganacias modelo nuevo': 111177.49786141906}

In [71]:

test_data_lgb['mae_modelo_actual'] = abs(test_data_lgb['ventas'] - test_data_lgb['modelo_actual'])
test_data_lgb['mae_predictions_tunned'] = abs(test_data_lgb['ventas'] - test_data_lgb['predictions_tunned'])


mae_por_producto = test_data_lgb.groupby('prod_id').agg({
    'mae_modelo_actual': 'mean',
    'mae_predictions_tunned': 'mean'
}).reset_index()


productos_peor_modelo = mae_por_producto.sort_values(by='mae_modelo_actual', ascending=False).head(100)
productos_peor_predictions_tunned = mae_por_producto.sort_values(by='mae_predictions_tunned', ascending=False).head(10)
productos_peor_modelo=productos_peor_modelo['prod_id'].unique()

In [72]:
import plotly.express as px

productos_filtrados = test_data_lgb[test_data_lgb['prod_id'].isin(productos_peor_modelo)]

fig = px.line(productos_filtrados, 
              x='fecha', 
              y='ventas', 
              color='prod_id', 
              title='Ventas por Producto',
              labels={'fecha': 'Fecha', 'ventas': 'Ventas'},
              markers=True)

fig.show()


El RMSE del modelo nuevo es menor que el del modelo actual , indicando que las predicciones del modelo ajustado tienen una menor variación con respecto a las ventas reales.También el modelo está explicando 40.52% de la variabilidad de los datos es explicada por el modelo, lo cual es un poco más alto que el modelo anterior (38%)

Este aumento en precisión se traduce en menos discrepancias entre lo predicho y las ventas reales, lo que lleva a una mejor planificación y asignación de recursos. Se puede observar que las predicciones del modelo pueden ya reflejar la estacionalidad marcada dentro del set de datos Y en los meses de Marzo - Junio deja de subestimar el inventario y puede predecir las bajas en el mismo a diferencia del modelo actual. La ganancia/pérdida promedio del modelo actual es negativa, lo que indica que está subestimando regularmente, mientras que el modelo ajustado se mueve a positivo. 

Estos sobre ajustes del modelo actual se pueden deber a productos específicos que tienen patrones muy particulares de ventas como se muestra en el análisis inferior por lo cuál los siguiente pasos podrían ser realizar modelos específicos para dichos productos y ver si el perfomance del modelo puede mejorar. 

Se eligió el modelo LightGBM  de manera autoregresiva y no modelos como ARIMA y SARIMA debido a la gran cantidad de productos disponibles dentro del inventario , la primera aproximación se quiso realizar con Prophet y el perfomance a nivel global fue considerablemente peor por lo cual se procedió a utilizar el el algoritmo LightGBM . 

### Predicciones para 2024

In [79]:
#Dado que el modelo requiere de intervalo de tiempos anteriores y está de manera mensual se realizará la predicción para el siguiente mes de 2024-01, con datos del mes anterior
df_pred_for2024=df_traininglgm.loc[df_traininglgm['fecha']=='2023-12-01']

In [81]:
x_pred_for2024=df_pred_for2024[['prod_id', 'rmean_ventas_1_3', 'rmean_ventas_1_12',
                                      'rmean_precio_promedio_1_3', 'mes_numero',
                                      'lag_1_ventas', 'lag_1_precio_promedio', 'ventas']]

preds_2024 = lgbm_tunned.predict(x_pred_for2024)

[LightGBM] [Warning] feature_fraction is set=0.784806087218487, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.784806087218487
[LightGBM] [Warning] bagging_fraction is set=0.8018252091633248, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8018252091633248
[LightGBM] [Warning] lambda_l2 is set=0.3585619546874841, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.3585619546874841
[LightGBM] [Warning] min_data_in_leaf is set=2, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=2


In [85]:
x_pred_for2024['Ventas_predicas_2024_01']=preds_2024

In [87]:
x_pred_for2024.to_csv('Predicciones_por_producto_202401.csv',encoding='utf-8', index=False)